# Imports

In [1]:
import folium  # map rendering library
from sklearn.cluster import KMeans  # import k-means from clustering stage
# Matplotlib and associated plotting modules
import matplotlib.colors as colors
import matplotlib.cm as cm
from bs4 import BeautifulSoup  # web scraping libraries and packages
# tranform JSON file into a pandas dataframe
from pandas.io.json import json_normalize
import requests  # library to handle requests
# convert an address into latitude and longitude values
from geopy.geocoders import Nominatim
import json  # library to handle JSON files
import numpy as np  # library to handle data in a vectorized manner
import pandas as pd  # library for data analsysis
pd.set_option('display.max_columns', None)
pd.set_option('display.max_rows', None)
print('Libraries imported.')

Libraries imported.


# Scraping the Wikipedia page

In [95]:
# GET request
toronto_data = requests.get(
    'https://en.wikipedia.org/wiki/List_of_postal_codes_of_Canada:_M').text
soup = BeautifulSoup(toronto_data, 'html.parser')
print('Data downloaded!')

Data downloaded!


# Wrangling and cleaning

In [96]:
postalCodes = []
boroughs = []
neighborhoods = []
# iterate each row of table and find postalcode, borough and neighborhood
for row in soup.find('table').find_all('tr'):
    cells = row.find_all('td')
    if(len(cells) > 0):
        postalCodes.append(cells[0].text.rstrip('\n'))
        boroughs.append(cells[1].text.rstrip('\n'))
        neighborhoods.append(cells[2].text.rstrip('\n'))
        

# Reading into dataframe with additional cleaning

In [97]:
df_toronto = pd.DataFrame({"PostalCode": postalCodes,
                           "Borough": boroughs,
                           "Neighborhood": neighborhoods})

# Filter borough and neighborhoods that are not asssigned
df_toronto = df_toronto[df_toronto.Borough != "Not assigned"].reset_index(drop=True)


def not_assigned_neighborhood(r):
    """
    Function to assign borough values for not assigned neighborhoods
    """
    if r['Neighborhood'] == "Not assigned":
        return r["Borough"]
    else:
        return r['Neighborhood']
        
# Assigning borough values to not assgned neighborhoods               
df_toronto["Neighborhood"] = df_toronto.apply(not_assigned_neighborhood,axis=1)


# Sanity check for the filter
assert len(df_toronto[df_toronto.Borough == "Not assigned"])==0
assert len(df_toronto[df_toronto.Neighborhood == "Not assigned"])==0

print('The dataframe has {} boroughs and {} neighborhoods.'.format(
        len(df_toronto['Borough'].unique()),
        df_toronto.shape[0]
    )
)

df_toronto.head()

The dataframe has 10 boroughs and 103 neighborhoods.


PostalCode           Borough                                 Neighborhood
0        M3A        North York                                    Parkwoods
1        M4A        North York                             Victoria Village
2        M5A  Downtown Toronto                    Regent Park, Harbourfront
3        M6A        North York             Lawrence Manor, Lawrence Heights
4        M7A  Downtown Toronto  Queen's Park, Ontario Provincial Government

In [5]:
df_toronto.shape

(103, 3)

# Reading the latitude and longitude from csv

In [6]:
lat_long = pd.read_csv('https://cocl.us/Geospatial_data')
lat_long.head()

Postal Code   Latitude  Longitude
0         M1B  43.806686 -79.194353
1         M1C  43.784535 -79.160497
2         M1E  43.763573 -79.188711
3         M1G  43.770992 -79.216917
4         M1H  43.773136 -79.239476

# Creating the required dataframe 

In [7]:
# Merging latitude and longitude data
df_toronto_coordinates = df_toronto.merge(lat_long, how='inner', left_on='PostalCode', right_on='Postal Code')
del df_toronto_coordinates['Postal Code']
# Changing order of columns
df_toronto_coordinates = df_toronto_coordinates[["PostalCode","Borough","Latitude","Longitude","Neighborhood"]]
df_toronto_coordinates.head()

# Concatenating neighborhoods for combination of other attributes
df_toronto_coordinates_grouped = df_toronto_coordinates.groupby(["PostalCode", "Borough","Latitude","Longitude"], as_index=False).agg(lambda x: ", ".join(x))

# For dataframe to display as per the question and in exact order
required_postcodes = ["M5G", "M2H", "M4B", "M1J", "M4G", "M4M", "M1R", "M9V", "M9L", "M5V", "M1B", "M5A"]
df_out = df_toronto_coordinates_grouped[df_toronto_coordinates_grouped['PostalCode'].isin(required_postcodes)].reset_index(drop=True)

df_output = pd.DataFrame()
for postcode in required_postcodes:
    df_output = df_output.append(df_out[df_out["PostalCode"]==postcode], ignore_index=True)
    
df_output

PostalCode           Borough   Latitude  Longitude  \
0         M5G  Downtown Toronto  43.657952 -79.387383   
1         M2H        North York  43.803762 -79.363452   
2         M4B         East York  43.706397 -79.309937   
3         M1J       Scarborough  43.744734 -79.239476   
4         M4G         East York  43.709060 -79.363452   
5         M4M      East Toronto  43.659526 -79.340923   
6         M1R       Scarborough  43.750072 -79.295849   
7         M9V         Etobicoke  43.739416 -79.588437   
8         M9L        North York  43.756303 -79.565963   
9         M5V  Downtown Toronto  43.628947 -79.394420   
10        M1B       Scarborough  43.806686 -79.194353   
11        M5A  Downtown Toronto  43.654260 -79.360636   

                                         Neighborhood  
0                                  Central Bay Street  
1                                   Hillcrest Village  
2                     Parkview Hill, Woodbine Gardens  
3                                 Scarborough Village  
4                                             Leaside  
5                                     Studio District  
6                                   Wexford, Maryvale  
7   South Steeles, Silverstone, Humbergate, Jamest...  
8                                       Humber Summit  
9   CN Tower, King and Spadina, Railway Lands, Har...  
10                                     Malvern, Rouge  
11                          Regent Park, Harbourfront

# Getting coordinates for Toronto

In [30]:
address = 'Toronto'

geolocator = Nominatim(user_agent='toronto-explorer')
location = geolocator.geocode(address)
latitude = location.latitude
longitude = location.longitude
print('The geograpical coordinate of Toronto are {}, {}.'.format(latitude, longitude))

The geograpical coordinate of Toronto are 43.6534817, -79.3839347.


# Getting dataframe for boroughs with word Toronto

In [98]:
# First seggregating the neighborhoods in each borough
def get_neighborhoods(c):
    """
    Get individual neighborhoods in each borough from merged string with comma delimiter
    """
    n = c.split(",")
    return n

df_toronto['Neighborhoods'] = df_toronto['Neighborhood'].apply(get_neighborhoods)
df_toronto = df_toronto.explode('Neighborhoods').reset_index(drop=True)
del df_toronto['Neighborhood']
df_toronto.rename(columns={'Neighborhoods':'Neighborhood'}, inplace=True)
df_toronto

PostalCode           Borough  \
0          M3A        North York   
1          M4A        North York   
2          M5A  Downtown Toronto   
3          M5A  Downtown Toronto   
4          M6A        North York   
5          M6A        North York   
6          M7A  Downtown Toronto   
7          M7A  Downtown Toronto   
8          M9A         Etobicoke   
9          M9A         Etobicoke   
10         M1B       Scarborough   
11         M1B       Scarborough   
12         M3B        North York   
13         M4B         East York   
14         M4B         East York   
15         M5B  Downtown Toronto   
16         M5B  Downtown Toronto   
17         M6B        North York   
18         M9B         Etobicoke   
19         M9B         Etobicoke   
20         M9B         Etobicoke   
21         M9B         Etobicoke   
22         M9B         Etobicoke   
23         M1C       Scarborough   
24         M1C       Scarborough   
25         M1C       Scarborough   
26         M3C        North York   
27         M4C         East York   
28         M5C  Downtown Toronto   
29         M6C              York   
30         M9C         Etobicoke   
31         M9C         Etobicoke   
32         M9C         Etobicoke   
33         M9C         Etobicoke   
34         M1E       Scarborough   
35         M1E       Scarborough   
36         M1E       Scarborough   
37         M4E      East Toronto   
38         M5E  Downtown Toronto   
39         M6E              York   
40         M1G       Scarborough   
41         M4G         East York   
42         M5G  Downtown Toronto   
43         M6G  Downtown Toronto   
44         M1H       Scarborough   
45         M2H        North York   
46         M3H        North York   
47         M3H        North York   
48         M3H        North York   
49         M4H         East York   
50         M5H  Downtown Toronto   
51         M5H  Downtown Toronto   
52         M5H  Downtown Toronto   
53         M6H      West Toronto   
54         M6H      West Toronto   
55         M1J       Scarborough   
56         M2J        North York   
57         M2J        North York   
58         M2J        North York   
59         M3J        North York   
60         M3J        North York   
61         M4J         East York   
62         M4J         East York   
63         M5J  Downtown Toronto   
64         M5J  Downtown Toronto   
65         M5J  Downtown Toronto   
66         M6J      West Toronto   
67         M6J      West Toronto   
68         M1K       Scarborough   
69         M1K       Scarborough   
70         M1K       Scarborough   
71         M2K        North York   
72         M3K        North York   
73         M4K      East Toronto   
74         M4K      East Toronto   
75         M5K  Downtown Toronto   
76         M5K  Downtown Toronto   
77         M6K      West Toronto   
78         M6K      West Toronto   
79         M6K      West Toronto   
80         M1L       Scarborough   
81         M1L       Scarborough   
82         M1L       Scarborough   
83         M2L        North York   
84         M2L        North York   
85         M3L        North York   
86         M4L      East Toronto   
87         M4L      East Toronto   
88         M5L  Downtown Toronto   
89         M5L  Downtown Toronto   
90         M6L        North York   
91         M6L        North York   
92         M6L        North York   
93         M9L        North York   
94         M1M       Scarborough   
95         M1M       Scarborough   
96         M1M       Scarborough   
97         M2M        North York   
98         M2M        North York   
99         M3M        North York   
100        M4M      East Toronto   
101        M5M        North York   
102        M5M        North York   
103        M6M              York   
104        M6M              York   
105        M6M              York   
106        M9M        North York   
107        M9M        North York   
108        M1N       Scarborough   
109        M1N       Scarborough   
110     

In [103]:
# Filtering out boroughs that do not have Toronto in name
boroughs = list(df_toronto.Borough.unique())

borough_with_toronto = []

for x in boroughs:
    if "toronto" in x.lower():
        borough_with_toronto.append(x)
        
# DataFrame with boroughs that contain the word Toronto
df_borugh_toronto = df_toronto[df_toronto['Borough'].isin(borough_with_toronto)].reset_index(drop=True)
print("Shape of the dataframe: ",df_borugh_toronto.shape)
df_borugh_toronto.head()

Shape of the dataframe:  (78, 3)


PostalCode           Borough                    Neighborhood
0        M5A  Downtown Toronto                     Regent Park
1        M5A  Downtown Toronto                    Harbourfront
2        M7A  Downtown Toronto                    Queen's Park
3        M7A  Downtown Toronto   Ontario Provincial Government
4        M5B  Downtown Toronto                 Garden District

In [105]:
# Geolocator does not find coordinates for each neighborhood
## so filtering out those
data = []
not_found_count = 0
geolocator = Nominatim(user_agent="toronto_explorer")
for index, row in df_toronto.iterrows():
    full_address = row['Neighborhood'] + ', Toronto'
    try:
        location = geolocator.geocode(full_address)
        data.append((row['PostalCode'],row['Borough'],row['Neighborhood'],location.latitude,location.longitude))
    except AttributeError:
        not_found_count += 1

df_main = pd.DataFrame(data)
df_main.columns = ['PostalCode','Borough','Neighborhood','Latitude','Longitude']

# Show in map

In [107]:
map_toronto = folium.Map(location=[latitude, longitude], zoom_start=10)

# add markers to map
for lat, lng, borough, neighborhood in zip(df_main['Latitude'],
                                           df_main['Longitude'],
                                           df_main['Borough'],
                                           df_main['Neighborhood']):
    label = '{}, {}'.format(neighborhood, borough)
    label = folium.Popup(label, parse_html=True)
    folium.CircleMarker(
        [lat, lng],
        radius=5,
        popup=label,
        color='blue',
        fill=True,
        fill_color='#3186cc',
        fill_opacity=0.7).add_to(map_toronto)

map_toronto

# Define Foursquare Credentials and Version

In [212]:
from getpass import getpass

CLIENT_ID = getpass("CLIENT_ID")
CLIENT_SECRET = getpass("CLIENT_SECRET")

VERSION = '20201223' # Foursquare API version

CLIENT_ID········
CLIENT_SECRET········


# Getting dataframe of top 100 venues within a radius of 500 m of the borough coordinates

In [109]:
radius = 500
LIMIT = 100

venues = []

for lat, long, post, borough, neighborhood in zip(df_main['Latitude'], 
                                                  df_main['Longitude'], 
                                                  df_main['PostalCode'], 
                                                  df_main['Borough'], 
                                                  df_main['Neighborhood']):
    url = 'https://api.foursquare.com/v2/venues/explore?&client_id={}&client_secret={}&v={}&ll={},{}&radius={}&limit={}'.format(
    CLIENT_ID,
    CLIENT_SECRET,
    VERSION,
    lat,
    long,
    radius, 
    LIMIT)
    results = requests.get(url).json()["response"]['groups'][0]['items']
    
    for venue in results:
        venues.append((
            post, 
            borough,
            neighborhood,
            lat, 
            long, 
            venue['venue']['name'], 
            venue['venue']['location']['lat'], 
            venue['venue']['location']['lng'],  
            venue['venue']['categories'][0]['name']))
        
df_venues = pd.DataFrame(venues)

df_venues.columns = ['PostalCode', 'Borough', 'Neighborhood', 'BoroughLatitude', 'BoroughLongitude', 'VenueName', 'VenueLatitude', 'VenueLongitude', 'VenueCategory']

df_venues.head()

PostalCode     Borough Neighborhood  BoroughLatitude  BoroughLongitude  \
0        M3A  North York    Parkwoods          43.7588        -79.320197   
1        M3A  North York    Parkwoods          43.7588        -79.320197   
2        M3A  North York    Parkwoods          43.7588        -79.320197   
3        M3A  North York    Parkwoods          43.7588        -79.320197   
4        M3A  North York    Parkwoods          43.7588        -79.320197   

            VenueName  VenueLatitude  VenueLongitude         VenueCategory  
0     Allwyn's Bakery      43.759840      -79.324719  Caribbean Restaurant  
1                LCBO      43.757774      -79.314257          Liquor Store  
2  Shoppers Drug Mart      43.760857      -79.324961              Pharmacy  
3        Petro-Canada      43.757950      -79.315187           Gas Station  
4         Pizza Pizza      43.760231      -79.325666           Pizza Place

In [110]:
# Venues returned for a combination of postalcode,borough and neighbourhood
df_venues.groupby(["PostalCode", "Borough", "Neighborhood"])['VenueName'].count().reset_index()

PostalCode           Borough                      Neighborhood  VenueName
0          M1B       Scarborough                             Rouge          2
1          M1B       Scarborough                           Malvern         13
2          M1C       Scarborough                    Highland Creek          4
3          M1C       Scarborough                        Port Union          2
4          M1C       Scarborough                        Rouge Hill          1
5          M1E       Scarborough                       Morningside         12
6          M1E       Scarborough                         West Hill         30
7          M1E       Scarborough                         Guildwood          4
8          M1G       Scarborough                            Woburn         21
9          M1H       Scarborough                         Cedarbrae         26
10         M1J       Scarborough               Scarborough Village          8
11         M1K       Scarborough              East Birchmount Park          4
12         M1K       Scarborough                           Ionview          4
13         M1K       Scarborough                      Kennedy Park          5
14         M1L       Scarborough                          Clairlea         11
15         M1L       Scarborough                          Oakridge          6
16         M1L       Scarborough                       Golden Mile         57
17         M1M       Scarborough                        Cliffcrest          5
18         M1M       Scarborough          Scarborough Village West          8
19         M1M       Scarborough                         Cliffside          7
20         M1N       Scarborough                    Cliffside West          7
21         M1N       Scarborough                       Birch Cliff          4
22         M1P       Scarborough           Scarborough Town Centre         40
23         M1P       Scarborough                   Wexford Heights         14
24         M1P       Scarborough                       Dorset Park          7
25         M1R       Scarborough                          Maryvale         22
26         M1R       Scarborough                           Wexford         19
27         M1S       Scarborough                         Agincourt         12
28         M1T       Scarborough                          Sullivan         22
29         M1T       Scarborough                     Tam O'Shanter         11
30         M1T       Scarborough                    Clarks Corners          3
31         M1V       Scarborough                   Agincourt North         27
32         M1V       Scarborough                   L'Amoreaux East          7
33         M1V       Scarborough                      Steeles East          2
34         M1V       Scarborough                          Milliken         41
35         M1W       Scarborough                   L'Amoreaux West          7
36         M1W       Scarborough                      Steeles West          2
37         M1X       Scarborough                       Upper Rouge          2
38         M2H        North York                 Hillcrest Village         44
39         M2J        North York                        Henry Farm          4
40         M2J        North York                            Oriole          9
41         M2J        North York                          Fairview         71
42         M2K        North York                   Bayview Village         12
43         M2L        North York                      Silver Hills          2
44         M2L        North York                        York Mills         16
45         M2M        North York                       Newtonbrook         34
46         M2M        North York                        Willowdale         47
47         M2N        North York                   Willowdale East         47
48         M2N        North York                        Willowdale         47
49         M2P        North York                   York Mills West         16
50         M2R        Nort

In [130]:
df_main.shape

(206, 5)

### There are 203 rows here but the main dataframe has 206. 

In [159]:
to_remove = [x for x in df_main['Neighborhood'].unique().tolist() if x not in df_venues['Neighborhood'].unique().tolist()]
df_main = df_main[df_main['Neighborhood'].isin(to_remove)==False]
df_main = df_main.reset_index(drop=True)
df_main.shape

(204, 6)

# Analyze each neighborhood

In [111]:
# one hot encoding
toronto_onehot = pd.get_dummies(df_venues[['VenueCategory']], prefix="", prefix_sep="")

# add postal, borough and neighborhood column back to dataframe
toronto_onehot['PostalCode'] = df_venues['PostalCode'] 
toronto_onehot['Borough'] = df_venues['Borough'] 
toronto_onehot['Neighborhoods'] = df_venues['Neighborhood'] 

# move postal, borough and neighborhood column to the first column
fixed_columns = list(toronto_onehot.columns[-3:]) + list(toronto_onehot.columns[:-3])
toronto_onehot = toronto_onehot[fixed_columns]

toronto_onehot.head()

PostalCode     Borough Neighborhoods  ATM  Accessories Store  \
0        M3A  North York     Parkwoods    0                  0   
1        M3A  North York     Parkwoods    0                  0   
2        M3A  North York     Parkwoods    0                  0   
3        M3A  North York     Parkwoods    0                  0   
4        M3A  North York     Parkwoods    0                  0   

   Afghan Restaurant  African Restaurant  Airport  Airport Service  \
0                  0                   0        0                0   
1                  0                   0        0                0   
2                  0                   0        0                0   
3                  0                   0        0                0   
4                  0                   0        0                0   

   Airport Terminal  American Restaurant  Animal Shelter  Antique Shop  \
0                 0                    0               0             0   
1                 0                    0               0             0   
2                 0                    0               0             0   
3                 0                    0               0             0   
4                 0                    0               0             0   

   Aquarium  Art Gallery  Art Museum  Arts & Crafts Store  \
0         0            0           0                    0   
1         0            0           0                    0   
2         0            0           0                    0   
3         0            0           0                    0   
4         0            0           0                    0   

   Arts & Entertainment  Asian Restaurant  Athletics & Sports  \
0                     0                 0                   0   
1                     0                 0                   0   
2                     0                 0                   0   
3                     0                 0                   0   
4                     0                 0                   0   

   Auto Dealership  Auto Workshop  Automotive Shop  BBQ Joint  Bagel Shop  \
0                0              0                0          0           0   
1                0              0                0          0           0   
2                0              0                0          0           0   
3                0              0                0          0           0   
4                0              0                0          0           0   

   Bakery  Bank  Bar  Baseball Field  Baseball Stadium  Basketball Stadium  \
0       0     0    0               0                 0                   0   
1       0     0    0               0                 0                   0   
2       0     0    0               0                 0                   0   
3       0     0    0               0                 0                   0   
4       0     0    0               0                 0                   0   

   Beach  Beach Bar  Bed & Breakfast  Beer Bar  Beer Store  \
0      0          0                0         0           0   
1      0          0                0         0           0   
2      0          0                0         0           0   
3      0          0                0         0           0   
4      0          0                0         0           0   

   Belgian Restaurant  Big Box Store  Bike Shop  Bike Trail  Bistro  \
0                   0              0          0           0       0   
1                   0              0          0           0       0   
2                   0              0          0           0       0   
3                   0              0          0           0       0   
4                   0              0          0           0       0   

   Boat or Ferry  Bookstore  Boutique  Bowling Alley  Brazilian Restaurant  \
0              0          0         0              0                     0   
1              0          0         0              0                     0   
2              

# Group rows by neighborhood and by taking the mean of the frequency of occurrence of each category

In [112]:
toronto_grouped = toronto_onehot.groupby(["PostalCode", "Borough", "Neighborhoods"]).mean().reset_index()
toronto_grouped

PostalCode           Borough                     Neighborhoods       ATM  \
0          M1B       Scarborough                             Rouge  0.000000   
1          M1B       Scarborough                           Malvern  0.000000   
2          M1C       Scarborough                    Highland Creek  0.000000   
3          M1C       Scarborough                        Port Union  0.000000   
4          M1C       Scarborough                        Rouge Hill  0.000000   
5          M1E       Scarborough                       Morningside  0.000000   
6          M1E       Scarborough                         West Hill  0.000000   
7          M1E       Scarborough                         Guildwood  0.000000   
8          M1G       Scarborough                            Woburn  0.000000   
9          M1H       Scarborough                         Cedarbrae  0.000000   
10         M1J       Scarborough               Scarborough Village  0.000000   
11         M1K       Scarborough              East Birchmount Park  0.000000   
12         M1K       Scarborough                           Ionview  0.000000   
13         M1K       Scarborough                      Kennedy Park  0.000000   
14         M1L       Scarborough                          Clairlea  0.000000   
15         M1L       Scarborough                          Oakridge  0.000000   
16         M1L       Scarborough                       Golden Mile  0.000000   
17         M1M       Scarborough                        Cliffcrest  0.000000   
18         M1M       Scarborough          Scarborough Village West  0.000000   
19         M1M       Scarborough                         Cliffside  0.000000   
20         M1N       Scarborough                    Cliffside West  0.000000   
21         M1N       Scarborough                       Birch Cliff  0.000000   
22         M1P       Scarborough           Scarborough Town Centre  0.000000   
23         M1P       Scarborough                   Wexford Heights  0.000000   
24         M1P       Scarborough                       Dorset Park  0.000000   
25         M1R       Scarborough                          Maryvale  0.000000   
26         M1R       Scarborough                           Wexford  0.000000   
27         M1S       Scarborough                         Agincourt  0.000000   
28         M1T       Scarborough                          Sullivan  0.000000   
29         M1T       Scarborough                     Tam O'Shanter  0.000000   
30         M1T       Scarborough                    Clarks Corners  0.000000   
31         M1V       Scarborough                   Agincourt North  0.000000   
32         M1V       Scarborough                   L'Amoreaux East  0.000000   
33         M1V       Scarborough                      Steeles East  0.000000   
34         M1V       Scarborough                          Milliken  0.000000   
35         M1W       Scarborough                   L'Amoreaux West  0.000000   
36         M1W       Scarborough                      Steeles West  0.000000   
37         M1X       Scarborough                       Upper Rouge  0.000000   
38         M2H        North York                 Hillcrest Village  0.000000   
39         M2J        North York                        Henry Farm  0.000000   
40         M2J        North York                            Oriole  0.000000   
41         M2J        North York                          Fairview  0.000000   
42         M2K        North York                   Bayview Village  0.000000   
43         M2L        North York                      Silver Hills  0.000000   
44         M2L        North York                        York Mills  0.000000   
45         M2M        North York                       Newtonbrook  0.000000   
46         M2M        North York                        Willowdale  0.000000   
47         M2N        North York                   Willowdale East  0.000000   
48         M2N        North York                        Willowdale  0.000000   
49  

# Each neighborhood along with the top 5 most common venues

In [150]:
num_top_venues = 5

indicators = ['st', 'nd', 'rd']

# create columns according to number of top venues
areaColumns = ['PostalCode', 'Borough', 'Neighborhoods']
freqColumns = []
for ind in np.arange(num_top_venues):
    try:
        freqColumns.append('{}{} Most Common Venue'.format(ind+1, indicators[ind]))
    except:
        freqColumns.append('{}th Most Common Venue'.format(ind+1))
columns = areaColumns+freqColumns

# create a new dataframe
neighborhoods_venues_sorted = pd.DataFrame(columns=columns)
neighborhoods_venues_sorted['PostalCode'] = toronto_grouped['PostalCode']
neighborhoods_venues_sorted['Borough'] = toronto_grouped['Borough']
neighborhoods_venues_sorted['Neighborhoods'] = toronto_grouped['Neighborhoods']

for ind in np.arange(toronto_grouped.shape[0]):
    row_categories = toronto_grouped.iloc[ind, :].iloc[3:]
    row_categories_sorted = row_categories.sort_values(ascending=False)
    neighborhoods_venues_sorted.iloc[ind, 3:] = row_categories_sorted.index.values[0:num_top_venues]

# neighborhoods_venues_sorted.sort_values(freqColumns, inplace=True)
print(neighborhoods_venues_sorted.shape)
neighborhoods_venues_sorted

(204, 8)


PostalCode           Borough                     Neighborhoods  \
0          M1B       Scarborough                             Rouge   
1          M1B       Scarborough                           Malvern   
2          M1C       Scarborough                    Highland Creek   
3          M1C       Scarborough                        Port Union   
4          M1C       Scarborough                        Rouge Hill   
5          M1E       Scarborough                       Morningside   
6          M1E       Scarborough                         West Hill   
7          M1E       Scarborough                         Guildwood   
8          M1G       Scarborough                            Woburn   
9          M1H       Scarborough                         Cedarbrae   
10         M1J       Scarborough               Scarborough Village   
11         M1K       Scarborough              East Birchmount Park   
12         M1K       Scarborough                           Ionview   
13         M1K       Scarborough                      Kennedy Park   
14         M1L       Scarborough                          Clairlea   
15         M1L       Scarborough                          Oakridge   
16         M1L       Scarborough                       Golden Mile   
17         M1M       Scarborough                        Cliffcrest   
18         M1M       Scarborough          Scarborough Village West   
19         M1M       Scarborough                         Cliffside   
20         M1N       Scarborough                    Cliffside West   
21         M1N       Scarborough                       Birch Cliff   
22         M1P       Scarborough           Scarborough Town Centre   
23         M1P       Scarborough                   Wexford Heights   
24         M1P       Scarborough                       Dorset Park   
25         M1R       Scarborough                          Maryvale   
26         M1R       Scarborough                           Wexford   
27         M1S       Scarborough                         Agincourt   
28         M1T       Scarborough                          Sullivan   
29         M1T       Scarborough                     Tam O'Shanter   
30         M1T       Scarborough                    Clarks Corners   
31         M1V       Scarborough                   Agincourt North   
32         M1V       Scarborough                   L'Amoreaux East   
33         M1V       Scarborough                      Steeles East   
34         M1V       Scarborough                          Milliken   
35         M1W       Scarborough                   L'Amoreaux West   
36         M1W       Scarborough                      Steeles West   
37         M1X       Scarborough                       Upper Rouge   
38         M2H        North York                 Hillcrest Village   
39         M2J        North York                        Henry Farm   
40         M2J        North York                            Oriole   
41         M2J        North York                          Fairview   
42         M2K        North York                   Bayview Village   
43         M2L        North York                      Silver Hills   
44         M2L        North York                        York Mills   
45         M2M        North York                       Newtonbrook   
46         M2M        North York                        Willowdale   
47         M2N        North York                   Willowdale East   
48         M2N        North York                        Willowdale   
49         M2P        North York                   York Mills West   
50         M2R        North York                   Willowdale West   
51         M2R        North York                        Willowdale   
52         M3A        North York                         Parkwoods   
53         M3B        North York                         Don Mills   
54         M3C        North York                         Don Mills   
55         M3H        North York                   Downsview North   
56         M3H

# Cluster

In [203]:
kclusters = 5

toronto_grouped_clustering = toronto_grouped.drop(["PostalCode", "Borough", "Neighborhoods"], 1)

# run k-means clustering
kmeans = KMeans(n_clusters=kclusters, random_state=0).fit(toronto_grouped_clustering)

# check cluster labels generated for each row in the dataframe
kmeans.labels_[0:10]

array([2, 0, 2, 3, 4, 0, 0, 4, 0, 0], dtype=int32)

In [204]:
#create a new dataframe that includes the cluster as well as the top 10 venues for each neighborhood.
toronto_merged = df_main.copy()

# add clustering labels
toronto_merged["Cluster Labels"] = kmeans.labels_
neighborhoods_venues_sorted.rename(columns={'Neighborhoods':'Neighborhood'}, inplace=True)


# merge toronto_grouped with toronto_data to add latitude/longitude for each neighborhood
#df_temp = neighborhoods_venues_sorted.drop(['Borough'],axis=1)
toronto_merged = toronto_merged.merge(neighborhoods_venues_sorted, on=['PostalCode','Borough','Neighborhood'])



print(toronto_merged.shape)
toronto_merged.head() 

(204, 11)


PostalCode           Borough      Neighborhood   Latitude  Longitude  \
0        M3A        North York         Parkwoods  43.758800 -79.320197   
1        M4A        North York  Victoria Village  43.732658 -79.311189   
2        M5A  Downtown Toronto       Regent Park  43.660706 -79.360457   
3        M5A  Downtown Toronto      Harbourfront  43.640080 -79.380150   
4        M6A        North York    Lawrence Manor  43.722079 -79.437507   

   Cluster Labels      1st Most Common Venue     2nd Most Common Venue  \
0               2          Convenience Store             Shopping Mall   
1               0  Middle Eastern Restaurant  Mediterranean Restaurant   
2               2                Coffee Shop                Restaurant   
3               3                Coffee Shop                      Café   
4               4                       Bank         Electronics Store   

  3rd Most Common Venue 4th Most Common Venue 5th Most Common Venue  
0                  Bank       Laundry Service  Caribbean Restaurant  
1       Thai Restaurant              Bus Line   Filipino Restaurant  
2       Thai Restaurant     Indian Restaurant       Auto Dealership  
3            Restaurant                 Hotel    Italian Restaurant  
4       Doctor's Office            Kids Store                  Park

In [205]:
# sort the results by Cluster Labels
print(toronto_merged.shape)
toronto_merged.sort_values(["Cluster Labels"], inplace=True)
toronto_merged

(204, 11)


PostalCode           Borough                      Neighborhood   Latitude  \
101        M9M        North York                         Humberlea  43.721317   
119        M5P   Central Toronto             Forest Hill Road Park  43.694677   
120        M6P      West Toronto                         High Park  43.653867   
121        M6P      West Toronto                The Junction South  43.665478   
122        M9P         Etobicoke                         Westmount  43.693640   
123        M1R       Scarborough                           Wexford  43.745377   
124        M1R       Scarborough                          Maryvale  43.759051   
125        M2R        North York                        Willowdale  43.761510   
126        M2R        North York                   Willowdale West  43.761510   
127        M4R   Central Toronto                North Toronto West  43.646547   
128        M4R   Central Toronto                     Lawrence Park  43.729199   
129        M5R   Central Toronto                         The Annex  43.670338   
130        M5R   Central Toronto                     North Midtown  43.705200   
131        M5R   Central Toronto                         Yorkville  43.671386   
132        M6R      West Toronto                          Parkdale  43.640495   
133        M6R      West Toronto                      Roncesvalles  43.651443   
135        M9R         Etobicoke                      St. Phillips  43.700048   
136        M9R         Etobicoke              Martin Grove Gardens  43.687311   
137        M9R         Etobicoke                  Richview Gardens  43.684834   
138        M1S       Scarborough                         Agincourt  43.785353   
118        M5P   Central Toronto          Forest Hill North & West  43.701028   
139        M4S   Central Toronto                        Davisville  43.697936   
117        M4P   Central Toronto                  Davisville North  43.697936   
115        M1P       Scarborough           Scarborough Town Centre  43.776134   
93         M1M       Scarborough          Scarborough Village West  43.743742   
94         M2M        North York                        Willowdale  43.761510   
95         M2M        North York                       Newtonbrook  43.793886   
96         M3M        North York                         Downsview  43.749299   
97         M4M      East Toronto                   Studio District  43.649585   
98         M5M        North York                      Bedford Park  43.737388   
99         M5M        North York               Lawrence Manor East  43.722079   
100        M6M              York                      Mount Dennis  43.686960   
202        M8Z         Etobicoke          Kingsway Park South West  43.647381   
102        M9M        North York                             Emery  43.752074   
103        M1N       Scarborough                       Birch Cliff  43.691805   
105        M2N        North York                        Willowdale  43.761510   
106        M2N        North York                   Willowdale East  43.761510   
107        M3N        North York                         Downsview  43.749299   
108        M4N   Central Toronto                     Lawrence Park  43.729199   
109        M5N   Central Toronto                          Roselawn  43.708710   
110        M6N              York                         Runnymede  43.651703   
112        M9N              York                            Weston  43.700161   
113        M1P       Scarborough                       Dorset Park  43.752847   
116        M2P        North York                   York Mills West  43.744039   
92         M1M       Scarborough                        Cliffcrest  43.721836   
140        M5S  Downtown Toronto             University of Toronto  43.663462   
142        M6S      West Toronto                         Runnymede  43.651703   
174        M9V         Etobicoke                       Thistletown  43.737266   
175        M9V         Etobicoke   

# Visualizing the clusters

In [206]:
map_clusters = folium.Map(location=[latitude, longitude], zoom_start=11)

# set color scheme for the clusters
x = np.arange(kclusters)
ys = [i+x+(i*x)**2 for i in range(kclusters)]
colors_array = cm.rainbow(np.linspace(0, 1, len(ys)))
rainbow = [colors.rgb2hex(i) for i in colors_array]

# add markers to the map
markers_colors = []
for lat, lon, post, bor, poi, cluster in zip(toronto_merged['Latitude'], toronto_merged['Longitude'], toronto_merged['PostalCode'], toronto_merged['Borough'], toronto_merged['Neighborhood'], toronto_merged['Cluster Labels']):
    label = folium.Popup('{} ({}): {} - Cluster {}'.format(bor, post, poi, cluster), parse_html=True)
    folium.CircleMarker(
        [lat, lon],
        radius=5,
        popup=label,
        color=rainbow[cluster-1],
        fill=True,
        fill_color=rainbow[cluster-1],
        fill_opacity=0.7).add_to(map_clusters)
       
map_clusters

# Examine Clusters

## Cluster 1: 

In [207]:
toronto_merged.loc[toronto_merged['Cluster Labels'] == 0, toronto_merged.columns[[1] + \
                                                                                 list(range(5, toronto_merged.shape[1]))]]

Borough  Cluster Labels        1st Most Common Venue  \
101        North York               0            Convenience Store   
119   Central Toronto               0                        Trail   
120      West Toronto               0                    Pet Store   
121      West Toronto               0                         Café   
122         Etobicoke               0                  Pizza Place   
123       Scarborough               0                  Pizza Place   
124       Scarborough               0                  Coffee Shop   
125        North York               0                  Coffee Shop   
126        North York               0                  Coffee Shop   
127   Central Toronto               0                          Bar   
128   Central Toronto               0             Sushi Restaurant   
129   Central Toronto               0                  Pizza Place   
130   Central Toronto               0                  Coffee Shop   
131   Central Toronto               0           Italian Restaurant   
132      West Toronto               0           Tibetan Restaurant   
133      West Toronto               0                         Café   
135         Etobicoke               0                         Park   
136         Etobicoke               0                     Pharmacy   
137         Etobicoke               0                 Home Service   
138       Scarborough               0                   Food Court   
118   Central Toronto               0                  Pizza Place   
139   Central Toronto               0           Italian Restaurant   
117   Central Toronto               0           Italian Restaurant   
115       Scarborough               0               Clothing Store   
93        Scarborough               0                  Coffee Shop   
94         North York               0                  Coffee Shop   
95         North York               0            Korean Restaurant   
96         North York               0                Metro Station   
97       East Toronto               0                  Coffee Shop   
98         North York               0         Gym / Fitness Center   
99         North York               0                         Bank   
100              York               0       Furniture / Home Store   
202         Etobicoke               0                  Coffee Shop   
102        North York               0                  Pizza Place   
103       Scarborough               0        General Entertainment   
105        North York               0                  Coffee Shop   
106        North York               0                  Coffee Shop   
107        North York               0                Metro Station   
108   Central Toronto               0             Sushi Restaurant   
109   Central Toronto               0                          Spa   
110              York               0                         Café   
112              York               0                Train Station   
113       Scarborough               0            Indian Restaurant   
116        North York               0                  Coffee Shop   
92        Scarborough               0               Ice Cream Shop   
140  Downtown Toronto               0                         Café   
142      West Toronto               0                         Café   
174         Etobicoke               0            Indian Restaurant   
175         Etobicoke               0                Grocery Store   
178  Downtown Toronto               0                   Playground   
179         Etobicoke               0                  Pizza Place   
180         Etobicoke               0           Light Rail Station   
181         Etobicoke               0                          Bar   
182         Etobicoke               0           Chinese Restaurant   
183       Scarborough               0                         Park   
188         Etobicoke               0                  Coffee Shop   
189         Etobicoke   

## Cluster 2: 

In [208]:
toronto_merged.loc[toronto_merged['Cluster Labels'] == 1, toronto_merged.columns[[1] + \
                                                                                 list(range(5, toronto_merged.shape[1]))]]

Borough  Cluster Labels 1st Most Common Venue  \
33        Scarborough               1                  Park   
36   Downtown Toronto               1           Coffee Shop   
201         Etobicoke               1            Restaurant   

    2nd Most Common Venue 3rd Most Common Venue 4th Most Common Venue  \
33            Coffee Shop           Supermarket  Fast Food Restaurant   
36             Restaurant                  Café    Italian Restaurant   
201   Sporting Goods Shop             BBQ Joint           Coffee Shop   

    5th Most Common Venue  
33         Discount Store  
36    Japanese Restaurant  
201    Italian Restaurant

## Cluster 3: 

In [209]:
toronto_merged.loc[toronto_merged['Cluster Labels'] == 2, toronto_merged.columns[[1] + \
                                                                                 list(range(5, toronto_merged.shape[1]))]]

Borough  Cluster Labels       1st Most Common Venue  \
12          East York               2  Construction & Landscaping   
2    Downtown Toronto               2                 Coffee Shop   
187  Downtown Toronto               2          Chinese Restaurant   
185  Downtown Toronto               2                        Café   
184  Downtown Toronto               2                 Coffee Shop   
177       Scarborough               2          Chinese Restaurant   
191  Downtown Toronto               2                 Coffee Shop   
39   Downtown Toronto               2                 Coffee Shop   
59          East York               2                        Park   
86   Downtown Toronto               2                 Coffee Shop   
84       East Toronto               2                       Beach   
104       Scarborough               2              Breakfast Spot   
111              York               2                        Café   
114       Scarborough               2   Middle Eastern Restaurant   
69         North York               2               Metro Station   
65        Scarborough               2        Fast Food Restaurant   
172         Etobicoke               2                     Airport   
134         Etobicoke               2                        Park   
43         North York               2           Korean Restaurant   
0          North York               2           Convenience Store   
145       Scarborough               2                 Pizza Place   
90         North York               2                      Bakery   
37        Scarborough               2        Fast Food Restaurant   
155       Scarborough               2          Chinese Restaurant   
166  Downtown Toronto               2                 Yoga Studio   
30          Etobicoke               2                     Dog Run   
165  Downtown Toronto               2                 Coffee Shop   
163  Downtown Toronto               2         Japanese Restaurant   

    2nd Most Common Venue        3rd Most Common Venue  \
12            Yoga Studio            Fish & Chips Shop   
2              Restaurant              Thai Restaurant   
187   Sporting Goods Shop                         Bank   
185           Coffee Shop                   Restaurant   
184                  Café                  Pizza Place   
177         Shopping Mall         Caribbean Restaurant   
191           Pizza Place                Grocery Store   
39                   Café               Sandwich Place   
59         Ice Cream Shop                      Theater   
86            Pizza Place                Grocery Store   
84                    Bar               Breakfast Spot   
104                   Pub                Auto Workshop   
111                   Bar              Thai Restaurant   
114     Indian Restaurant                Grocery Store   
69                   Park       Furniture / Home Store   
65     Chinese Restaurant                Grocery Store   
172      Airport Terminal                  Yoga Studio   
134           Yoga Studio  Eastern European Restaurant   
43          Grocery Store                  Coffee Shop   
0           Shopping Mall                         Bank   
145                  Bank              Thai Restaurant   
90             Restaurant                         Park   
37         Discount Store                  Coffee Shop   
155         Shopping Mall         Caribbean Restaurant   
166          Dessert Shop                         Café   
30            Flower Shop                  Gas Station   
165                  Café                Grocery Store   
163           Coffee Shop                   Food Court   

           4th Most Common Venue 5th Most Common Venue  
12             Electronics Store  Ethiopian Restaurant  
2              Indian Restaurant       Auto Dealership  
187               Breakfast Spot           Gas Station  
185            Indian Restaurant    Italian Restaurant  
184                Grocery Store            

## Cluster 4: 

In [210]:
toronto_merged.loc[toronto_merged['Cluster Labels'] == 3, toronto_merged.columns[[1] + \
                                                                                 list(range(5, toronto_merged.shape[1]))]]

Borough  Cluster Labels       1st Most Common Venue  \
3    Downtown Toronto               3                 Coffee Shop   
195         Etobicoke               3  Construction & Landscaping   
186  Downtown Toronto               3                 Coffee Shop   

    2nd Most Common Venue 3rd Most Common Venue 4th Most Common Venue  \
3                    Café            Restaurant                 Hotel   
195                  Pool                  Park           Yoga Studio   
186                 Hotel                  Café            Restaurant   

    5th Most Common Venue  
3      Italian Restaurant  
195                 Field  
186   Japanese Restaurant

## Cluster 5: 

In [211]:
toronto_merged.loc[toronto_merged['Cluster Labels'] == 4, toronto_merged.columns[[1] + \
                                                                                 list(range(5, toronto_merged.shape[1]))]]

Borough  Cluster Labels 1st Most Common Venue  \
4         North York               4                  Bank   
158  Central Toronto               4        Sandwich Place   
7          Etobicoke               4           Yoga Studio   
66       Scarborough               4         Metro Station   
176      Scarborough               4            Playground   
168        Etobicoke               4           Coffee Shop   

          2nd Most Common Venue 3rd Most Common Venue 4th Most Common Venue  \
4             Electronics Store       Doctor's Office            Kids Store   
158              History Museum                  Café           Coffee Shop   
7            Italian Restaurant         Deli / Bodega                  Park   
66   Construction & Landscaping         Deli / Bodega                  Park   
176     Health & Beauty Service                 Field   Egyptian Restaurant   
168                        Café    Mexican Restaurant     Indian Restaurant   

    5th Most Common Venue  
4                    Park  
158     Indian Restaurant  
7             Coffee Shop  
66      Fish & Chips Shop  
176     Electronics Store  
168                   Gym